### Libraries

In [3]:
from sklearn.datasets import load_breast_cancer
import numpy as np
import random
import diffprivlib
from tqdm import tqdm
from sklearn.metrics import accuracy_score
from diffprivlib.models import LogisticRegression as DP_LogisticRegression
from diffprivlib.models import GaussianNB as DPGaussianNB  
from diffprivlib.models import DecisionTreeClassifier as DP_DecisionTreeClassifier
from diffprivlib.models import RandomForestClassifier as DP_RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.base import clone
from sklearn.preprocessing import LabelEncoder
import math
from scipy.special import softmax
from sklearn.datasets import make_classification
import scipy.stats as stats
import time
from decimal import Decimal
import pickle
import os

### Nonprivate models

In [4]:
def get_nonprivate_model(model_name, random_state):
    

    if model_name == "Random_forest":
        model= RandomForestClassifier(random_state=random_state)
        
        
    elif model_name == "Decision_tree":
        model=DecisionTreeClassifier()
    
        
    elif model_name == "Naive_bayes":
       model=GaussianNB()
        
    elif model_name == "Logistic_regression":
        model=LogisticRegression(max_iter=5000, random_state=random_state)
    return model

### Private models

In [5]:
def get_private_model(model_name, X_train, y_train, y, epsilon):
    EPSILON =epsilon
  
    classes = np.unique(y)

    if model_name == "Random_forest":
        # Define bounds for each feature (for differential privacy)
        min_bounds = -20
        max_bounds = 20
        bounds = (min_bounds, max_bounds)
        
        # Initialize private Random Forest with differential privacy
        model = DP_RandomForestClassifier(
            epsilon=EPSILON,    # Differential privacy parameter
            n_estimators=127,   # Number of trees in the forest
            max_depth=7,        # Maximum depth of the trees
            bounds=bounds,      # Data bounds for differential privacy
            random_state=42,
            classes=classes
        )
    elif model_name == "Decision_tree":
        # Define bounds for each feature (for differential privacy)
        min_bounds = -20
        max_bounds = 20
        bounds = (min_bounds, max_bounds)
    
        # Initialize private Random Forest with differential privacy
        model = DP_DecisionTreeClassifier(
            epsilon=EPSILON,    # Differential privacy parameter
            max_depth=6,        # Maximum depth of the trees
            bounds=bounds,      # Data bounds for differential privacy
            random_state=42,
            classes=classes
        )
    elif model_name == "Naive_bayes":
        # Define bounds for each feature (for differential privacy)
        min_bounds =-20 
        max_bounds =20 
        bounds = (min_bounds, max_bounds)
        
        # Initialize private Naive Bayes with differential privacy
        model = DPGaussianNB(
            epsilon=EPSILON,    # Differential privacy parameter
            bounds=bounds,      # Data bounds for differential privacy
            random_state=42
        )
    elif model_name == "Logistic_regression":
        # Calculate the data norm (L2 norm)
        data_norm = 20
        
        # Initialize private Logistic Regression
        model = DP_LogisticRegression(
            epsilon=EPSILON,
            data_norm=data_norm,
            random_state=42
        )
    return model    

### Performance evaluation function

In [6]:
# Updated evaluation function to include accuracy
def evaluate_conformal_split(prediction_sets, y_test, y_pred):
    # Calculate coverage
    coverage = np.mean([1 if y_test[i] in prediction_sets[i] else 0 for i in range(len(y_test))])

    # Calculate Efficiency
    ambiguities = [len(pred_set) for pred_set in prediction_sets]
    average_Efficiency = np.mean(ambiguities)

    # Calculate accuracy
    accuracy = np.mean(y_test == y_pred)

    return coverage, average_Efficiency, accuracy

### Helping function for PCOQS method

In [7]:
def NoisyRC(range_bounds, D, sigma):
    """
    Noisy Range Count for float values with Gaussian noise.

    Parameters:
    range_bounds (tuple): A tuple (a, b) representing the range [a, b].
    D (list): The sorted dataset.
    sigma (float): The standard deviation of the Gaussian noise.

    Returns:
    int: The noisy count of elements in the range [a, b].
    """
    a, b = range_bounds
    count = sum(1 for z in D if a <= z <= b)
    noise = np.random.normal(0, sigma)
    noisy_count = count + noise
    return max(0, int(np.floor(noisy_count)))  # Ensure non-negative count

def PCOQS(D, alpha, rho, seed, lower_bound=0, upper_bound=1, delta=1e-10):
    """
    Differentially Private Quantile Approximation Algorithm without integer conversion.

    Parameters:
    D (list): The sorted dataset.
    alpha (float): The quantile level (e.g., 0.5 for median).
    rho (float): The privacy parameter (smaller = more private).
    lower_bound (float): Lower bound of the search space.
    upper_bound (float): Upper bound of the search space.
    delta (float): Small positive value to ensure convergence.

    Returns:
    float: A differentially private approximation of the quantile x_{(m)}.
    """

    
    n = len(D)
    max_iterations = int(np.ceil(np.log2((upper_bound - lower_bound) / delta)))
    sigma = np.sqrt(max_iterations / (2 * rho)) # Noise scale for Gaussian mechanism
    m = int(np.ceil((1 - alpha) * (n + 1)))

    left, right = lower_bound, upper_bound
    random.seed(seed)
    for i in range(max_iterations):
        mid = (left + right) / 2
        c = NoisyRC((lower_bound, mid), D, sigma)
        
        if c < m:
            left = mid + delta
        else:
            right = mid

    return np.round((left + right) / 2, 2)



### Helping function for EXPONQ method

In [8]:
# Optimal gamma is a root.
def get_optimal_gamma(scores,n,alpha,m,epsilon):
    a = alpha**2
    b = - ( alpha*epsilon*(n+1)*(1-alpha)/2 + 2*alpha )
    c = 1
    best_q = 1
    gamma1 = (-b + np.sqrt(b**2 - 4*a*c))/(2*a)
    gamma2 = (-b - np.sqrt(b**2 - 4*a*c))/(2*a)

    gamma1 = min(max(gamma1,1e-12),1-1e-12)
    gamma2 = min(max(gamma2,1e-12),1-1e-12)

    bins = np.linspace(0,1,m)

    q1 = get_private_quantile(scores, alpha, epsilon, gamma1, bins)
    q2 = get_private_quantile(scores, alpha, epsilon, gamma2, bins)

    return (gamma1, q1) if q1 < q2 else (gamma2, q2)

def get_optimal_gamma_m(n, alpha, epsilon):
    candidates_m = np.logspace(4,6,50).astype(int)
    scores = np.random.rand(n,1)
    best_m = int(1/alpha)
    best_gamma = 1
    best_q = 1
    for m in candidates_m:
        gamma, q = get_optimal_gamma(scores,n,alpha,m,epsilon)
        if q < best_q:
            best_q = q
            best_m = m
            best_gamma = gamma
    return best_m, best_gamma

def get_private_quantile(scores, alpha, epsilon, gamma, bins):
    n = scores.shape[0]
    epsilon_normed = epsilon*min(alpha, 1-alpha)
    # Get the quantile
    qtilde = get_qtilde(n, alpha, gamma, epsilon, bins.shape[0])
    scores = scores.squeeze()
    score_to_bin = np.digitize(scores,bins)
    binned_scores = bins[np.minimum(score_to_bin,bins.shape[0]-1)]
    w1 = np.digitize(binned_scores, bins)
    w2 = np.digitize(binned_scores, bins, right=True)
    # Clip bins
    w1 = np.maximum(np.minimum(w1,bins.shape[0]-1),0)
    w2 = np.maximum(np.minimum(w2,bins.shape[0]-1),0)
    lower_mass = np.bincount(w1,minlength=bins.shape[0]).cumsum()/qtilde
    upper_mass = (n-np.bincount(w2,minlength=bins.shape[0]).cumsum())/(1-qtilde)
    w = np.maximum( lower_mass , upper_mass )
    sampling_probabilities = softmax(-(epsilon_normed/2)*w)
    # Check
    sampling_probabilities = sampling_probabilities/sampling_probabilities.sum()
    qhat = np.random.choice(bins,p=sampling_probabilities)
    return qhat

def get_shat_from_scores_private(scores, alpha, epsilon, gamma, score_bins):
    shat = get_private_quantile(scores, alpha, epsilon, gamma, score_bins)
    return shat

def get_qtilde(n,alpha,gamma,epsilon,m):
    qtilde = (n+1)*(1-alpha)/(n*(1-gamma*alpha))+2/(epsilon*n)*np.log(m/(gamma*alpha))
    qtilde = min(qtilde, 1-1e-12)
    return qtilde

### Helping function for Histogram + Laplace Method

In [9]:
def dp_quantile_noisy_hist(x, q, epsilon, seed, bins=50, domain=(0.0, 1.0), rng=None):
    """
    Differentially private quantile using a Laplace-noised histogram (ε-DP).

    Args:
        x (array-like): data vector (numeric).
        q (float): desired quantile in (0,1).
        epsilon (float): privacy budget for the entire histogram.
        domain (tuple): (lo, hi) public bounds for clipping/binning.
        bins (int): number of fixed, public bins.
        rng: np.random.Generator (optional).

    Returns:
        float: DP quantile estimate (can lie between data points).

    Privacy & assumptions:
        - Data are clipped to the public domain (lo, hi).
        - Build a fixed-bin histogram, add Lap(1/ε) noise to each bin count.
        - Because each record contributes to exactly one bin, releasing
          the full noisy histogram is ε-DP under add/remove adjacency.
        - Quantile is computed from the noisy cumulative counts.

    Notes:
        - Works best if a reasonable public domain is known.
        - For stability, negative noisy counts are floored at 0.
    """
    x = np.asarray(x, dtype=float)
    if x.size == 0:
        raise ValueError("x must be non-empty.")
    if not (0 < q < 1):
        raise ValueError("q must be in (0,1).")
    if epsilon <= 0:
        raise ValueError("epsilon must be > 0.")
    if rng is None:
        rng = np.random.default_rng(seed)

    lo, hi = domain
    if not (lo < hi):
        raise ValueError("domain must satisfy lo < hi.")

    # Clip to public domain
    xc = np.clip(x, lo, hi)

    # Fixed public bins
    edges = np.linspace(lo, hi, bins + 1)
    #print(f"Bins: {edges}")
    counts, _ = np.histogram(xc, bins=edges)
    #print(f"Counts of histogram: {counts}")

    # Laplace noise to each bin (scale = 1/ε)
    noise = rng.laplace(loc=0.0, scale=1.0/epsilon, size=bins)
    #print(f"Noise for each bin: {noise}")
    noisy = np.maximum(counts + noise, 0.0)
    #print(noisy)

    # Cumulative proportion
    csum = np.cumsum(noisy)
    if csum[-1] <= 0:
        # extremely unlikely unless ε is tiny and n is tiny
        return float(np.median(xc))

    target = q * csum[-1]
    j = np.searchsorted(csum, target)  # first bin reaching the target

    j = int(np.clip(j, 0, bins - 1))
    # Linear interpolation within the bin (simple, uniform-within-bin)
    bin_lo, bin_hi = edges[j], edges[j + 1]
    prev = csum[j - 1] if j > 0 else 0.0
    within = (target - prev) / max(noisy[j], 1e-12)
    within = np.clip(within, 0.0, 1.0)
    return float(bin_lo + within * (bin_hi - bin_lo))

### Data generation

In [10]:
def simulate_normal_classification(
    n_samples_per_class,
    n_features,
    n_classes,
    class_means=None,
    class_covariances=None,
    random_state=None
):
    """
    Simulate classification data directly from Normal distributions.
    
    Parameters:
        n_samples_per_class (int): Number of samples per class.
        n_features (int): Number of features.
        n_classes (int): Number of classes.
        class_means (list of arrays): List of mean vectors for each class. If None, generated randomly.
        class_covariances (list of arrays): List of covariance matrices for each class. If None, identity matrices are used.
        random_state (int): Seed for reproducibility.
    
    Returns:
        X (ndarray): Feature matrix of shape (n_samples, n_features), rounded to 4 decimal places.
        y (ndarray): Class labels of shape (n_samples,), rounded to 4 decimal places.
    """
    np.random.seed(random_state)
    
    X = []
    y = []
    
    # Generate means and covariances if not provided
    if class_means is None:
        class_means = [np.random.uniform(-5, 5, n_features) for _ in range(n_classes)]
    if class_covariances is None:
        class_covariances = [np.eye(n_features) for _ in range(n_classes)]
    
    for class_idx in range(n_classes):
        # Draw samples from the Normal distribution
        samples = np.random.multivariate_normal(
            mean=class_means[class_idx],
            cov=class_covariances[class_idx],
            size=n_samples_per_class
        )
        X.append(samples)
        y.extend([class_idx] * n_samples_per_class)
    
    # Combine data and shuffle
    X = np.vstack(X)
    y = np.array(y)
    indices = np.random.permutation(len(y))
    
    # Round X and y to 4 decimal places
    X = np.round(X[indices], 4)
    y = np.round(y[indices], 4)
    
    return X, y


### Simulation function

In [11]:
def run_simulation(
    private_model,
    private_conformal,
    model_name,
    n_samples_per_class,
    n_features,
    n_classes,
    class_means,
    class_covariances,
    alpha,
    epsilon,
    conformal_epsilon,
    n_trials,
    seed
):
    n_trials = int(n_trials)

    # Result containers
    coverage_results_anas = []
    Efficiency_results_anas = []
    informativeness_results_anas = []
    quantile_error_results_anas = []

    coverage_results_PCOQS = []
    Efficiency_results_PCOQS = []
    informativeness_results_PCOQS = []
    quantile_error_results_PCOQS = []

    coverage_results_Lap_hist = []
    Efficiency_results_Lap_hist = []
    informativeness_results_Lap_hist = []
    quantile_error_results_Lap_hist = []

    coverage_results_np = []
    Efficiency_results_np = []
    informativeness_results_np = []

    accuracy_results = []

    for i in tqdm(range(n_trials)):
        seed = seed +i

        # Step 1: generate data
        X, y = simulate_normal_classification(
            n_samples_per_class=n_samples_per_class,
            n_features=n_features,
            n_classes=n_classes,
            class_means=class_means,
            class_covariances=class_covariances,
            random_state=i + 3
        )

        # Step 2: split
        X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.4, random_state=i + 3)
        X_cal, X_test, y_cal, y_test = train_test_split(X_temp, y_temp, test_size=0.4, random_state=i + 3)
        num_calib = len(X_cal)

        # Train model
        if private_model:
            model = get_private_model(model_name, X_train, y_train,y, epsilon) 
        else:
            model = get_nonprivate_model(model_name, random_state=42)

        model.fit(X_train, y_train)

        # Calibration scores (NO rounding)
        prob_cal = model.predict_proba(X_cal)
        scores_cal = 1 - prob_cal[np.arange(len(y_cal)), y_cal]

        # -----------------------------------------------------------
        # Compute non-private empirical quantile (baseline)
        # -----------------------------------------------------------
        n_cal = len(scores_cal)
        q_np = np.ceil((n_cal + 1) * (1 - alpha)) / n_cal
        empirical_quantile = np.quantile(scores_cal, q_np)

        # -----------------------------------------------------------
        # Differentially private conformal thresholds
        # -----------------------------------------------------------
        if private_conformal:
            # EXPONQ threshold
            mstar, gammastar = get_optimal_gamma_m(num_calib, alpha, conformal_epsilon)
            score_bins = np.linspace(0, 1, mstar)
            threshold_anas = get_shat_from_scores_private(scores_cal, alpha, conformal_epsilon, gammastar, score_bins)

            # PCOQS threshold
            sorted_scores = np.sort(scores_cal)
            rho = conformal_epsilon**2 / 2
            threshold_PCOQS = PCOQS(sorted_scores, alpha, rho, seed)

            # Laplace histogram threshold
            q = 1 - alpha
            rng = np.random.default_rng(i + 21)
            threshold_Lap_hist = dp_quantile_noisy_hist(
                sorted_scores, q, conformal_epsilon, seed, domain=(0.0, 1.0), bins=50, rng=rng
            )

            # -------------------------------------------------------
            # Quantile error = |DP quantile - empirical quantile|
            # -------------------------------------------------------
            quantile_error_results_anas.append(abs(threshold_anas - empirical_quantile))
            quantile_error_results_PCOQS.append(abs(threshold_PCOQS - empirical_quantile))
            quantile_error_results_Lap_hist.append(abs(threshold_Lap_hist - empirical_quantile))

        else:
            # Non-private
            threshold = empirical_quantile  # already correct split-conformal form

        # -----------------------------------------------------------
        # Prediction sets
        # -----------------------------------------------------------
        prob_test = model.predict_proba(X_test)
        scores_test = 1 - prob_test

        if private_conformal:
            # EXPONQ prediction sets
            prediction_sets_anas = [
                np.where(scores <= threshold_anas)[0] for scores in scores_test
            ]
            prediction_sets_anas = [ps if len(ps) > 0 else [-1] for ps in prediction_sets_anas]
            informativeness_results_anas.append(np.mean([len(ps) == 1 for ps in prediction_sets_anas]))

            # PCOQS sets
            prediction_sets_PCOQS = [
                np.where(scores <= threshold_PCOQS)[0] for scores in scores_test
            ]
            prediction_sets_PCOQS = [ps if len(ps) > 0 else [-1] for ps in prediction_sets_PCOQS]
            informativeness_results_PCOQS.append(np.mean([len(ps) == 1 for ps in prediction_sets_PCOQS]))

            # Lap_hist sets
            prediction_sets_Lap_hist = [
                np.where(scores <= threshold_Lap_hist)[0] for scores in scores_test
            ]
            prediction_sets_Lap_hist = [ps if len(ps) > 0 else [-1] for ps in prediction_sets_Lap_hist]
            informativeness_results_Lap_hist.append(np.mean([len(ps) == 1 for ps in prediction_sets_Lap_hist]))

        else:
            # Non-private sets
            prediction_sets = [
                np.where(scores <= threshold)[0] for scores in scores_test
            ]
            prediction_sets = [ps if len(ps) > 0 else [-1] for ps in prediction_sets]
            informativeness_results_np.append(np.mean([len(ps) == 1 for ps in prediction_sets]))

        # -----------------------------------------------------------
        # Coverage and efficiency
        # -----------------------------------------------------------
        if private_conformal:
            # EXPONQ
            cov_anas = np.mean([y_test[j] in prediction_sets_anas[j] for j in range(len(y_test))])
            coverage_results_anas.append(cov_anas)
            Efficiency_results_anas.append(np.mean([len(ps) for ps in prediction_sets_anas]))

            # PCOQS
            cov_PCOQS = np.mean([y_test[j] in prediction_sets_PCOQS[j] for j in range(len(y_test))])
            coverage_results_PCOQS.append(cov_PCOQS)
            Efficiency_results_PCOQS.append(np.mean([len(ps) for ps in prediction_sets_PCOQS]))

            # Lap_hist
            cov_Lap = np.mean([y_test[j] in prediction_sets_Lap_hist[j] for j in range(len(y_test))])
            coverage_results_Lap_hist.append(cov_Lap)
            Efficiency_results_Lap_hist.append(np.mean([len(ps) for ps in prediction_sets_Lap_hist]))
        else:
            cov_np = np.mean([y_test[j] in prediction_sets[j] for j in range(len(y_test))])
            coverage_results_np.append(cov_np)
            Efficiency_results_np.append(np.mean([len(ps) for ps in prediction_sets]))

        # Accuracy
        accuracy_results.append(accuracy_score(y_test, model.predict(X_test)))

    # -----------------------------------------------------------
    # Aggregate final results
    # -----------------------------------------------------------
    results = {}

    if private_conformal:
        results["anas"] = {
            "coverage_mean": np.mean(coverage_results_anas),
            "coverage_std": np.std(coverage_results_anas, ddof=1),
            "Efficiency_mean": np.mean(Efficiency_results_anas),
            "Efficiency_std": np.std(Efficiency_results_anas, ddof=1),
            "informativeness_mean": np.mean(informativeness_results_anas),
            "informativeness_std": np.std(informativeness_results_anas, ddof=1),
            "quantile_error_mean": np.mean(quantile_error_results_anas),
            "quantile_error_std": np.std(quantile_error_results_anas, ddof=1)
        }

        results["PCOQS"] = {
            "coverage_mean": np.mean(coverage_results_PCOQS),
            "coverage_std": np.std(coverage_results_PCOQS, ddof=1),
            "Efficiency_mean": np.mean(Efficiency_results_PCOQS),
            "Efficiency_std": np.std(Efficiency_results_PCOQS, ddof=1),
            "informativeness_mean": np.mean(informativeness_results_PCOQS),
            "informativeness_std": np.std(informativeness_results_PCOQS, ddof=1),
            "quantile_error_mean": np.mean(quantile_error_results_PCOQS),
            "quantile_error_std": np.std(quantile_error_results_PCOQS, ddof=1)
        }

        results["Lap_hist"] = {
            "coverage_mean": np.mean(coverage_results_Lap_hist),
            "coverage_std": np.std(coverage_results_Lap_hist, ddof=1),
            "Efficiency_mean": np.mean(Efficiency_results_Lap_hist),
            "Efficiency_std": np.std(Efficiency_results_Lap_hist, ddof=1),
            "informativeness_mean": np.mean(informativeness_results_Lap_hist),
            "informativeness_std": np.std(informativeness_results_Lap_hist, ddof=1),
            "quantile_error_mean": np.mean(quantile_error_results_Lap_hist),
            "quantile_error_std": np.std(quantile_error_results_Lap_hist, ddof=1)
        }

    else:
        results["nonprivate"] = {
            "coverage_mean": np.mean(coverage_results_np),
            "coverage_std": np.std(coverage_results_np, ddof=1),
            "Efficiency_mean": np.mean(Efficiency_results_np),
            "Efficiency_std": np.std(Efficiency_results_np, ddof=1),
            "informativeness_mean": np.mean(informativeness_results_np),
            "informativeness_std": np.std(informativeness_results_np, ddof=1)
        }

    results["accuracy"] = {
        "mean": np.mean(accuracy_results),
        "std": np.std(accuracy_results, ddof=1),
    }

    return results


### Simulation function for different models

In [12]:
def complete_model_conformal_simulation(
    model_sets,
    private_models,
    private_conformals,
    n_samples_per_class,
    n_features,
    n_classes,
    class_means,
    class_covariances,
    alpha,
    epsilon,
    conformal_epsilon,
    n_trials,
    seed
):
    # Results dictionary to store all results
    results = {}

    for model_name in tqdm(model_sets):
        model_results = []

        for private_model in private_models:
            for private_conformal in private_conformals:

                sim_results = run_simulation(
                    private_model,
                    private_conformal,
                    model_name,
                    n_samples_per_class,
                    n_features,
                    n_classes,
                    class_means,
                    class_covariances,
                    alpha,
                    epsilon,
                    conformal_epsilon,
                    n_trials,
                    seed
                )

                acc_mean = sim_results["accuracy"]["mean"]
                acc_std = sim_results["accuracy"]["std"]

                if private_conformal:

                    # ----------- EXPONQ -----------
                    model_results.append({
                        "Description":
                            f"{model_name} | PM={private_model}, PC={private_conformal} | EXPONQ",
                        "Coverage":
                            f"{sim_results['anas']['coverage_mean']:.4f} ± {sim_results['anas']['coverage_std']:.4f}",
                        "Efficiency":
                            f"{sim_results['anas']['Efficiency_mean']:.4f} ± {sim_results['anas']['Efficiency_std']:.4f}",
                        "Informativeness":
                            f"{sim_results['anas']['informativeness_mean']:.4f} ± {sim_results['anas']['informativeness_std']:.4f}",
                        "Quantile Error":
                            f"{sim_results['anas']['quantile_error_mean']:.4f} ± {sim_results['anas']['quantile_error_std']:.4f}",
                        "Accuracy":
                            f"{acc_mean:.4f} ± {acc_std:.4f}",
                    })

                    # ----------- PCOQS -----------
                    model_results.append({
                        "Description":
                            f"{model_name} | PM={private_model}, PC={private_conformal} | PCOQS",
                        "Coverage":
                            f"{sim_results['PCOQS']['coverage_mean']:.4f} ± {sim_results['PCOQS']['coverage_std']:.4f}",
                        "Efficiency":
                            f"{sim_results['PCOQS']['Efficiency_mean']:.4f} ± {sim_results['PCOQS']['Efficiency_std']:.4f}",
                        "Informativeness":
                            f"{sim_results['PCOQS']['informativeness_mean']:.4f} ± {sim_results['PCOQS']['informativeness_std']:.4f}",
                        "Quantile Error":
                            f"{sim_results['PCOQS']['quantile_error_mean']:.4f} ± {sim_results['PCOQS']['quantile_error_std']:.4f}",
                        "Accuracy":
                            f"{acc_mean:.4f} ± {acc_std:.4f}",
                    })

                    # ----------- Laplace Histogram -----------
                    model_results.append({
                        "Description":
                            f"{model_name} | PM={private_model}, PC={private_conformal} | Lap_hist",
                        "Coverage":
                            f"{sim_results['Lap_hist']['coverage_mean']:.4f} ± {sim_results['Lap_hist']['coverage_std']:.4f}",
                        "Efficiency":
                            f"{sim_results['Lap_hist']['Efficiency_mean']:.4f} ± {sim_results['Lap_hist']['Efficiency_std']:.4f}",
                        "Informativeness":
                            f"{sim_results['Lap_hist']['informativeness_mean']:.4f} ± {sim_results['Lap_hist']['informativeness_std']:.4f}",
                        "Quantile Error":
                            f"{sim_results['Lap_hist']['quantile_error_mean']:.4f} ± {sim_results['Lap_hist']['quantile_error_std']:.4f}",
                        "Accuracy":
                            f"{acc_mean:.4f} ± {acc_std:.4f}",
                    })

                else:
                    # ----------- NON-PRIVATE CONFORMAL -----------
                    model_results.append({
                        "Description":
                            f"{model_name} | PM={private_model}, PC={private_conformal}",
                        "Coverage":
                            f"{sim_results['nonprivate']['coverage_mean']:.4f} ± {sim_results['nonprivate']['coverage_std']:.4f}",
                        "Efficiency":
                            f"{sim_results['nonprivate']['Efficiency_mean']:.4f} ± {sim_results['nonprivate']['Efficiency_std']:.4f}",
                        "Informativeness":
                            f"{sim_results['nonprivate']['informativeness_mean']:.4f} ± {sim_results['nonprivate']['informativeness_std']:.4f}",
                        "Accuracy":
                            f"{acc_mean:.4f} ± {acc_std:.4f}",
                    })

        results[model_name] = model_results

    # ---------------- PRINT SUMMARY ---------------- #
    for model_name, rows in results.items():
        print(f"\n{'#'*12}  {model_name}  {'#'*12}")
        print(f"{'Description':<85} {'Coverage':<20} {'Efficiency':<20} "
              f"{'Informativeness':<20} {'Quantile Error':<20} {'Accuracy':<20}")
        print("-" * 175)

        for r in rows:
            print(
                f"{r['Description']:<85} "
                f"{r['Coverage']:<20} "
                f"{r['Efficiency']:<20} "
                f"{r['Informativeness']:<20} "
                f"{r.get('Quantile Error', 'N/A'):<20} "
                f"{r['Accuracy']:<20}"
            )

        print("\n")

    return results


### Simulation function over CP epsilon values

In [13]:
def compare_conformal_epsilon(
    model_sets,
    epsilon,
    conformal_epsilon_values,
    private_models,
    private_conformals,
    n_samples_per_class,
    n_features,
    n_classes,
    class_means,
    class_covariances,
    alpha,
    n_trials,
    seed
):
    results = []  # Use a list to store the results
    for conformal_epsilon in  conformal_epsilon_values:
        print("conformal_epsilon:", conformal_epsilon)
        #rho = conformal_epsilon
        output = complete_model_conformal_simulation(
                                                    model_sets,
                                                    private_models,
                                                    private_conformals,
                                                    n_samples_per_class,
                                                    n_features,
                                                    n_classes,
                                                    class_means,
                                                    class_covariances,
                                                    alpha,
                                                    epsilon,
                                                    conformal_epsilon,
                                                    n_trials,
                                                    seed
                                                    )
        # Append results for the current conformal_epsilon
        results.append({"conformal_epsilon": conformal_epsilon, "output": output})
    return results


### Running the simulation

In [16]:
#Private model for different epsilon values and Nonprivate conformal 

model_sets = ["Naive_bayes",  "Random_forest"] 
private_models = [False, True]
private_conformals = [False, True]

n_samples_per_class=5000
n_features = 8
n_classes = 2
class_means = [
                np.array([0.8, 0.8, 0.8, 0.8, 0.8,0.8, 0.8, 0.8]), 
                np.array([-1, -1, -1, -1, -1, -1, -1, -1])
]
class_covariances = [
    np.eye(8)*7,
    np.eye(8) * 8,
     #np.eye(8) * 15,
]

n_trials =1000
alpha =  0.1
epsilon =2
conformal_epsilon_values = [0.1, 0.5, 1,1.5,3, 5, 10]
seed =123



results = compare_conformal_epsilon(
    model_sets,
    epsilon,
    conformal_epsilon_values,
    private_models,
    private_conformals,
    n_samples_per_class,
    n_features,
    n_classes,
    class_means,
    class_covariances,
    alpha,
    n_trials,
    seed
)

print(results)



conformal_epsilon: 0.1


100%|███████████████████████████████████████| 1000/1000 [00:11<00:00, 88.86it/s]

100%|███████████████████████████████████████| 1000/1000 [13:35<00:00,  1.23it/s]

100%|███████████████████████████████████████| 1000/1000 [00:20<00:00, 48.12it/s]

100%|███████████████████████████████████████| 1000/1000 [14:25<00:00,  1.16it/s]

100%|███████████████████████████████████████| 1000/1000 [27:44<00:00,  1.66s/it]

100%|███████████████████████████████████████| 1000/1000 [13:57<00:00,  1.19it/s]

100%|█████████████████████████████████████████| 2/2 [1:53:04<00:00, 3392.40s/it]



############  Naive_bayes  ############
Description                                                                           Coverage             Efficiency           Informativeness      Quantile Error       Accuracy            
-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Naive_bayes | PM=False, PC=False                                                      0.9004 ± 0.0098      1.1783 ± 0.0196      0.8217 ± 0.0196      N/A                  0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | EXPONQ                                              0.9999 ± 0.0004      1.9678 ± 0.0289      0.0322 ± 0.0289      0.3372 ± 0.0154      0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | PCOQS                                               0.9005 ± 0.0190      1.1813 ± 0.0529      0.8187 ± 0.0529      0.0316 ± 0.0251      0.8253 ± 0.0092     
Naive_bayes | PM=Fa

100%|███████████████████████████████████████| 1000/1000 [00:11<00:00, 84.70it/s]

100%|███████████████████████████████████████| 1000/1000 [13:05<00:00,  1.27it/s]

100%|███████████████████████████████████████| 1000/1000 [00:20<00:00, 48.89it/s]

100%|███████████████████████████████████████| 1000/1000 [14:30<00:00,  1.15it/s]

100%|███████████████████████████████████████| 1000/1000 [26:57<00:00,  1.62s/it]

100%|███████████████████████████████████████| 1000/1000 [21:12<00:00,  1.27s/it]

100%|█████████████████████████████████████████| 2/2 [2:05:09<00:00, 3754.97s/it]



############  Naive_bayes  ############
Description                                                                           Coverage             Efficiency           Informativeness      Quantile Error       Accuracy            
-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Naive_bayes | PM=False, PC=False                                                      0.9004 ± 0.0098      1.1783 ± 0.0196      0.8217 ± 0.0196      N/A                  0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | EXPONQ                                              0.9444 ± 0.0174      1.3465 ± 0.0972      0.6535 ± 0.0972      0.1199 ± 0.0512      0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | PCOQS                                               0.9005 ± 0.0103      1.1787 ± 0.0220      0.8213 ± 0.0220      0.0067 ± 0.0056      0.8253 ± 0.0092     
Naive_bayes | PM=Fa

...


############  Naive_bayes  ############
Description                                                                           Coverage             Efficiency           Informativeness      Quantile Error       Accuracy            
-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Naive_bayes | PM=False, PC=False                                                      0.9004 ± 0.0098      1.1783 ± 0.0196      0.8217 ± 0.0196      N/A                  0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | EXPONQ                                              0.9081 ± 0.0097      1.2019 ± 0.0213      0.7981 ± 0.0213      0.0194 ± 0.0078      0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | PCOQS                                               0.9006 ± 0.0099      1.1789 ± 0.0200      0.8211 ± 0.0200      0.0028 ± 0.0019      0.8253 ± 0.0092     
Naive_bayes | PM=Fa

100%|███████████████████████████████████████| 1000/1000 [00:12<00:00, 79.53it/s]

100%|███████████████████████████████████████| 1000/1000 [12:48<00:00,  1.30it/s]

100%|███████████████████████████████████████| 1000/1000 [00:23<00:00, 43.40it/s]

100%|███████████████████████████████████████| 1000/1000 [14:13<00:00,  1.17it/s]

100%|███████████████████████████████████████| 1000/1000 [26:43<00:00,  1.60s/it]

100%|███████████████████████████████████████| 1000/1000 [49:15<00:00,  2.96s/it]

100%|█████████████████████████████████████████| 2/2 [3:00:23<00:00, 5411.97s/it]



############  Naive_bayes  ############
Description                                                                           Coverage             Efficiency           Informativeness      Quantile Error       Accuracy            
-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Naive_bayes | PM=False, PC=False                                                      0.9004 ± 0.0098      1.1783 ± 0.0196      0.8217 ± 0.0196      N/A                  0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | EXPONQ                                              0.9051 ± 0.0097      1.1925 ± 0.0203      0.8075 ± 0.0203      0.0118 ± 0.0050      0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | PCOQS                                               0.9006 ± 0.0099      1.1788 ± 0.0200      0.8212 ± 0.0200      0.0026 ± 0.0017      0.8253 ± 0.0092     
Naive_bayes | PM=Fa

100%|███████████████████████████████████████| 1000/1000 [00:11<00:00, 84.48it/s]

100%|███████████████████████████████████████| 1000/1000 [11:58<00:00,  1.39it/s]

100%|███████████████████████████████████████| 1000/1000 [00:23<00:00, 43.19it/s]

100%|███████████████████████████████████████| 1000/1000 [14:15<00:00,  1.17it/s]

100%|███████████████████████████████████████| 1000/1000 [26:10<00:00,  1.57s/it]

100%|███████████████████████████████████████| 1000/1000 [56:06<00:00,  3.37s/it]

100%|█████████████████████████████████████████| 2/2 [3:12:14<00:00, 5767.11s/it]


############  Naive_bayes  ############
Description                                                                           Coverage             Efficiency           Informativeness      Quantile Error       Accuracy            
-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
Naive_bayes | PM=False, PC=False                                                      0.9004 ± 0.0098      1.1783 ± 0.0196      0.8217 ± 0.0196      N/A                  0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | EXPONQ                                              0.9029 ± 0.0097      1.1857 ± 0.0198      0.8143 ± 0.0198      0.0061 ± 0.0030      0.8253 ± 0.0092     
Naive_bayes | PM=False, PC=True | PCOQS                                               0.9006 ± 0.0099      1.1788 ± 0.0201      0.8212 ± 0.0201      0.0026 ± 0.0016      0.8253 ± 0.0092     
Naive_bayes | PM=Fa

In [18]:
import pickle as pkl
save_path = 'rank_error_results.pkl'
with open(save_path, 'wb') as f:
            pkl.dump(results, f)



In [19]:
# Load df_list from disk
with open('rank_error_results.pkl', 'rb') as f:
    rank_error_results = pkl.load(f)

In [20]:
rank_error_results

[{'conformal_epsilon': 0.1,
  'output': {'Naive_bayes': [{'Description': 'Naive_bayes | PM=False, PC=False',
     'Coverage': '0.9004 ± 0.0098',
     'Efficiency': '1.1783 ± 0.0196',
     'Informativeness': '0.8217 ± 0.0196',
     'Accuracy': '0.8253 ± 0.0092'},
    {'Description': 'Naive_bayes | PM=False, PC=True | EXPONQ',
     'Coverage': '0.9999 ± 0.0004',
     'Efficiency': '1.9678 ± 0.0289',
     'Informativeness': '0.0322 ± 0.0289',
     'Quantile Error': '0.3372 ± 0.0154',
     'Accuracy': '0.8253 ± 0.0092'},
    {'Description': 'Naive_bayes | PM=False, PC=True | PCOQS',
     'Coverage': '0.9005 ± 0.0190',
     'Efficiency': '1.1813 ± 0.0529',
     'Informativeness': '0.8187 ± 0.0529',
     'Quantile Error': '0.0316 ± 0.0251',
     'Accuracy': '0.8253 ± 0.0092'},
    {'Description': 'Naive_bayes | PM=False, PC=True | Lap_hist',
     'Coverage': '0.9074 ± 0.0192',
     'Efficiency': '1.2029 ± 0.0560',
     'Informativeness': '0.7971 ± 0.0560',
     'Quantile Error': '0.0372 ± 0.

### Processing the result for table presentation


You may ignor this part of the code as it is just for processing and displaying the result.

In [21]:
import pandas as pd

# Extract and filter data
filtered_data = []
for entry in results:
    epsilon = entry.get('conformal_epsilon', None)
    for model, model_data in entry.get('output', {}).items():
        for config in model_data:
            description = config.get('Description', '')
            if "Private Conformal: True" in description:
                if "EXPONQ" in description:
                    method = "E"
                elif "PCOQS" in description:
                    method = "P"
                elif "Lap_hist" in description:
                    method = "L"
                else:
                    method = "U"
                
                is_private_model = "Private Model: True" in description
                
                filtered_data.append({
                    'Model': model,
                    'Private_Model': is_private_model,
                    'epsilon_CP': epsilon,
                    'Method': method,
                    'C': config.get('Coverage', ''),
                    'E': config.get('Efficiency', ''),
                    'I': config.get('Informativeness', '')
                })

# Create DataFrame
df = pd.DataFrame(filtered_data)

# Display ultra-compact tables
def display_ultra_compact_tables():
    models = df['Model'].unique()
    
    for model in models:
        for is_private in [False, True]:
            subset = df[(df['Model'] == model) & (df['Private_Model'] == is_private)]
            
            if subset.empty:
                continue
                
            # Pivot table
            table = subset.pivot(index='epsilon_CP', columns='Method', 
                                values=['C', 'E', 'I'])
            
            # Single character columns: Metric_Method
            table.columns = [f"{col[0]}_{col[1]}" for col in table.columns]
            table = table.reset_index()
            
            # Ensure all columns exist
            methods = ['E', 'P', 'L']
            for metric in ['C', 'E', 'I']:
                for method in methods:
                    col_name = f"{metric}_{method}"
                    if col_name not in table.columns:
                        table[col_name] = "N/A"
            
            # Order columns
            column_order = ['epsilon_CP']
            for metric in ['C', 'E', 'I']:
                for method in methods:
                    column_order.append(f"{metric}_{method}")
            
            table = table[column_order].sort_values('epsilon_CP')
            
            privacy_status = "Private" if is_private else "Non-private"
            header = f"{model} - {privacy_status}"
            print(header)
            print("=" * len(header))
            
            # Ultra-compact header
            print(f"{'eps':>4} {'C_E':>14} {'C_P':>14} {'C_L':>14} {'E_E':>14} {'E_P':>14} {'E_L':>14} {'I_E':>14} {'I_P':>14} {'I_L':>14}")
            print("-" * 130)
            
            for _, row in table.iterrows():
                row_str = f"{row['epsilon_CP']:>4.1f} "
                for col in column_order[1:]:
                    row_str += f"{row[col]:>14} "
                print(row_str)
            print()

# Even more compact - single line per metric
def display_single_line_tables():
    models = df['Model'].unique()
    
    for model in models:
        for is_private in [False, True]:
            subset = df[(df['Model'] == model) & (df['Private_Model'] == is_private)]
            
            if subset.empty:
                continue
                
            table = subset.pivot(index='epsilon_CP', columns='Method', 
                                values=['C', 'E', 'I'])
            table.columns = [f"{col[0]}_{col[1]}" for col in table.columns]
            table = table.reset_index()
            
            methods = ['E', 'P', 'L']
            for metric in ['C', 'E', 'I']:
                for method in methods:
                    col_name = f"{metric}_{method}"
                    if col_name not in table.columns:
                        table[col_name] = "N/A"
            
            table = table.sort_values('epsilon_CP')
            
            privacy_status = "Private" if is_private else "Non-private"
            header = f"{model} - {privacy_status}"
            print(header)
            print("=" * len(header))
            
            # Print each epsilon with all data on one line
            for _, row in table.iterrows():
                eps_line = f"ε={row['epsilon_CP']:>3.1f} | "
                for metric in ['C', 'E', 'I']:
                    metric_line = f"{metric}: "
                    for method in ['E', 'P', 'L']:
                        metric_line += f"{method}={row[f'{metric}_{method}']} "
                    eps_line += metric_line + "| "
                print(eps_line)
            print()

# Super compact - minimal spacing
def display_super_compact():
    models = df['Model'].unique()
    
    for model in models:
        for is_private in [False, True]:
            subset = df[(df['Model'] == model) & (df['Private_Model'] == is_private)]
            if subset.empty: continue
                
            table = subset.pivot(index='epsilon_CP', columns='Method', values=['C', 'E', 'I'])
            table.columns = [f"{col[0]}{col[1]}" for col in table.columns]  # CE, CP, CL, EE, EP, EL, IE, IP, IL
            table = table.reset_index()
            
            # Ensure all columns
            methods = ['E', 'P', 'L']
            for metric in ['C', 'E', 'I']:
                for method in methods:
                    col_name = f"{metric}{method}"
                    if col_name not in table.columns:
                        table[col_name] = "N/A"
            
            table = table.sort_values('epsilon_CP')
            
            print(f"{model} - {'Private' if is_private else 'Non-private'}")
            print("=" * (len(model) + 11))
            
            # Minimal header
            print(f"{'ε':>3}  {'CE':>12} {'CP':>12} {'CL':>12}  {'EE':>12} {'EP':>12} {'EL':>12}  {'IE':>12} {'IP':>12} {'IL':>12}")
            print("-" * 125)
            
            for _, row in table.iterrows():
                line = f"{row['epsilon_CP']:>3.1f}  "
                line += f"{row['CE']:>12} {row['CP']:>12} {row['CL']:>12}  "
                line += f"{row['EE']:>12} {row['EP']:>12} {row['EL']:>12}  "
                line += f"{row['IE']:>12} {row['IP']:>12} {row['IL']:>12}"
                print(line)
            print()

# Use the most compact version
display_super_compact()

Naive_bayes - Non-private
  ε            CE           CP           CL            EE           EP           EL            IE           IP           IL
-----------------------------------------------------------------------------------------------------------------------------
0.1  0.9999 ± 0.0004 0.9005 ± 0.0190 0.9066 ± 0.0199  1.9678 ± 0.0289 1.1813 ± 0.0529 1.2005 ± 0.0559  0.0322 ± 0.0289 0.8187 ± 0.0529 0.7995 ± 0.0559
0.5  0.9444 ± 0.0174 0.9005 ± 0.0103 0.9001 ± 0.0108  1.3465 ± 0.0972 1.1787 ± 0.0220 1.1778 ± 0.0243  0.6535 ± 0.0972 0.8213 ± 0.0220 0.8222 ± 0.0243
1.0  0.9227 ± 0.0116 0.9005 ± 0.0101 0.9002 ± 0.0100  1.2509 ± 0.0360 1.1788 ± 0.0206 1.1779 ± 0.0205  0.7491 ± 0.0360 0.8212 ± 0.0206 0.8221 ± 0.0205
1.5  0.9154 ± 0.0103 0.9006 ± 0.0099 0.9002 ± 0.0099  1.2254 ± 0.0267 1.1789 ± 0.0201 1.1776 ± 0.0202  0.7746 ± 0.0267 0.8211 ± 0.0201 0.8224 ± 0.0202
3.0  0.9081 ± 0.0097 0.9006 ± 0.0099 0.9002 ± 0.0098  1.2019 ± 0.0213 1.1789 ± 0.0200 1.1777 ± 0.0197  0.7981 ± 0.0213 0

In [22]:


# # Extract and filter data
# filtered_data = []
# for entry in results:
#     epsilon = entry['conformal_epsilon']
#     for model, model_data in entry['output'].items():
#         for config in model_data:
#             if "Private Conformal: True" in config['Description']:
#                 method = "EXPONQ" if "EXPONQ" in config['Description'] else "PCOQS"
#                 is_private_model = "Private Model: True" in config['Description']
#                 filtered_data.append({
#                     'Model': model,
#                     'Private_Model': is_private_model,
#                     'epsilon_CP': epsilon,
#                     'Method': method,
#                     'Coverage': config['Coverage'],
#                     'Efficiency': config['Efficiency'],
#                     'Informativeness': config['Informativeness']
#                 })

# # Create DataFrame
# df = pd.DataFrame(filtered_data)

# # Function to create the table for a specific model and privacy setting
# def create_table(model_name, is_private):
#     # Filter data
#     subset = df[(df['Model'] == model_name) & (df['Private_Model'] == is_private)]
    
#     # Pivot the table properly
#     table = subset.pivot(index='epsilon_CP', columns='Method', 
#                         values=['Coverage', 'Efficiency', 'Informativeness'])
    
#     # Flatten multi-index columns
#     table.columns = [f"{col[0]} ({col[1]})" for col in table.columns]
#     table = table.reset_index()
    
#     # Reorder columns
#     column_order = [
#         'epsilon_CP',
#         'Coverage (EXPONQ)', 'Coverage (PCOQS)',
#         'Efficiency (EXPONQ)', 'Efficiency (PCOQS)',
#         'Informativeness (EXPONQ)', 'Informativeness (PCOQS)'
#     ]
#     table = table[column_order]
    
#     # Print header
#     privacy_status = "Private Model" if is_private else "Non-private Model"
#     print(f"\n{model_name} - {privacy_status}")
#     print("="*(len(model_name) + len(privacy_status) + 3))
    
#     return table.sort_values('epsilon_CP')

# # Example usage:
# print(create_table('Naive_bayes', False).to_string(index=False))
# print(create_table('Naive_bayes', True).to_string(index=False))
# print(create_table('Random_forest', False).to_string(index=False))
# print(create_table('Random_forest', True).to_string(index=False))